# Reconstructing Terrains: Scattered 2D Interpolation
In this exercise, we will do interpolation of height values associated with scattered data points. Scattered simply means that the data points are not organized in a grid which would make interpolation somewhat simpler. Instead, we will use the radial basis functions method.

In [ ]:
from pygel3d import hmesh, jupyter_display as jd, spatial
import numpy as np
from math import log, exp
from scipy.linalg import solve
import plotly.offline as py
import plotly.graph_objs as go
jd.set_export_mode(True)
array = np.array

### Create a grid
This function maps positions in a 2D grid into 3D by sampling a height map. 

`make_grid` takes three arguments: `dom_x` and `dom_y` are tuples containing the start end points in the x and y domain of the height map respectively. `hfun` is the height map represented as a function that returns z coordinate when passed x and y. `make_grid` returns `XV`, `YV`, and `ZV` as a tuple. All three are 2D arrays containing the X, Y, and Z coordinates of the gridded height map respectively.

In [ ]:
def make_grid(dom_x,dom_y, hfun):
    X = np.linspace(*dom_x,int(150.0*dom_x[1]))
    Y = np.linspace(*dom_y,int(150.0*dom_y[1]))
    XV,YV = np.meshgrid(X,Y)
    ZV = np.zeros(XV.shape)
    for i,j in np.ndindex(XV.shape):
        ZV[i,j] = hfun(XV[i,j], YV[i,j])
    return XV, YV, ZV

### Convert a 2D grid to a quad mesh
This function accepts a grid represented as three 2D arrays containing X, Y, and Z positions of each grid point. For each quadrilateral in the grid, we now create a face that is added to a new `Manifold`. Finally, the faces are stitched and the mesh is cleaned (removing the redundant vertices) and the mesh is finally returned.

In [ ]:
def mesh_grid(XV,YV,ZV):
    m = hmesh.Manifold()
    def g2c(i,j):
        return [XV[i,j],YV[i,j],ZV[i,j]]
    for i,j in np.ndindex(tuple(n-1 for n in XV.shape)):
        m.add_face([g2c(i,j), g2c(i,j+1), g2c(i+1,j+1), g2c(i+1,j)])
    hmesh.stitch(m)
    m.cleanup()
    return m

### Filtering points
The first function, `create_2d_tree`, puts the points into a k-D tree. This data structure makes it possible to find points that are close to another point efficiently.

`filter_points` function takes a bunch of points. For each point that has not been visited, it marks as visited all points within a small radius of that point. In this way, we avoid duplicate points which would otherwise cause numerical issues.

In [ ]:
def create_2d_tree(pts):
    tree = spatial.I3DTree()
    for i in range(0,len(pts)):
        p = array(pts[i])
        p[2] = 0
        tree.insert(p,i)
    tree.build()
    return tree

def filter_points(coords, rad):
    tree = create_2d_tree(coords)
    new_coords = []
    visited = [False]*len(coords)
    for i in range(0,len(coords)):
        if not visited[i]:
            p = array(coords[i])
            new_coords += [array(p)]
            p[2] = 0
            (K,V) = tree.in_sphere(p,rad)
            for idx in V:
                visited[idx] = True
    return new_coords

### Draw a grid using Plotly
Plotly has a specific function for height maps (Surface) which makes it easy to visualize contours. We use this one in addition to our mesh visualization technique.

In [ ]:
def draw_hm(XV,YV,ZV):
    contour = go.Surface(x=XV,y=YV,z=ZV,contours=dict(z=dict(show=True)))
    lyt = go.Layout(width=850,height=600)
    lyt.scene.aspectmode="data"
    lyt.scene.zaxis.nticks = 10
    fig = go.Figure(data=[contour],layout=lyt)
    py.iplot(fig)

### Load and filter points
The code below loads a point set and transforms it to a domain that fits inside the unit cube. This makes numerics more robust. The coordinates could be very big which might lead to floating point errors.

In [ ]:
f = open("./kote1-sorted.txt")
lines = f.readlines()
coords = []
for l in lines:
    coords += [list(map(float, l.split()))]
point_mat = np.array(coords)
spanx = point_mat[:,0].max() - point_mat[:,0].min()
spany = point_mat[:,1].max() - point_mat[:,1].min()
span = max(spanx,spany)
coords -= np.array([point_mat[:,0].min(),point_mat[:,1].min(),point_mat[:,2].min()])
coords *= array([1.,1.,5.])/span
coords = filter_points(coords, 0.001)

## Part 1: Gaussian RBF

Reconstruct the terrain using gaussian radial basis functions. This involves constructing the `A` matrix below and implementing the function that sums the radial basis functions (evaluated at the given point) weighted with the coefficient you compute.


In [12]:
# We provide the Gaussian RBF below. Since we will need to evaluate rbf_gaussian 
# with a value r=length(v) for a vector, v, and we really use the square of r, r^2, 
# we opt instead to call the function with v directly and compute r^2 as the dot 
# product of v with itself, i.e. r^2 = <v, v>
def rbf_gaussian(v):
    inv_scale = 1000
    return exp(-v@v*inv_scale)

N = len(coords)
A = np.zeros((N,N))
b = np.zeros(N)
### ---- Insert code here ----
# Below, fill the matrix A such that entry i,j is the value of the Gaussian RBF
# centered at i and evaluated at j. Also, construct the right hand side, i.e. the 
# b vector.
for i in range(N):
    for j in range(N):
        A[i][j] = rbf_gaussian(coords[i][:2] - coords[j][:2])
print("A has been constructed")
b = [coords[i][2] for i in range(N)]
# The regularization below where a small constant time the identity 
# is added is essential to making the Gaussian radial basis functions work.
A += 0.001 * np.eye(N)


# Finally, solve for the coefficients
s_height = np.linalg.solve(A, b)
### --------


def rbf_height_fun(x, y):
    ### ---- Insert code here ----
    # Below, sum the radial basis functions evaluated at x,y and weighted with the 
    # coefficients just computed.
    radials = [rbf_gaussian(np.array([x, y]) - p_coords[:2]) for p_coords in coords]
    h = np.dot(radials, s_height)
    return h
    ### --------
print("got coefficients")
XV,YV,ZV= make_grid((0,spanx/span),(0,spany/span), rbf_height_fun)
print(XV)
print(YV)
print(ZV)
draw_hm(XV,YV,ZV)

A has been constructed
got coefficients
[[0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]
 [0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]
 [0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]
 ...
 [0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]
 [0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]
 [0.         0.00677098 0.01354197 ... 0.42657195 0.43334293 0.44011392]]
[[0.         0.         0.         ... 0.         0.         0.        ]
 [0.00671141 0.00671141 0.00671141 ... 0.00671141 0.00671141 0.00671141]
 [0.01342282 0.01342282 0.01342282 ... 0.01342282 0.01342282 0.01342282]
 ...
 [0.98657718 0.98657718 0.98657718 ... 0.98657718 0.98657718 0.98657718]
 [0.99328859 0.99328859 0.99328859 ... 0.99328859 0.99328859 0.99328859]
 [1.         1.         1.         ... 1.         1.         1.        ]]
[[ 1.74416519e-19  1.58308969e-18  1.29986202e-17 ... -2.81515863e-06
  

'hi'

### Part 1.2: Variations
Explore what effect `inv_scale` in `rbf_gaussian` has on the reconstruction. Try to set the value to something that is 10 times greater or smaller and watch what happens.

## Part 2: Create an RBF height map:
Find the coefficients of a Thin Plate Spline radial basis function interpolation of the terrain points. This is very similar to what you just did, but using the TPS RBF instead of the Gaussian.

In [1]:
def rbf(v):
    ### ---- Insert code here ----
    
    # Return the value of the Thin Plate Spline rbf
    r = v@v
    return (0.5*r*log(r))
    ### ---- Solution end ----

N = len(coords)
A = np.zeros((N+3,N+3))
b = np.zeros(N+3)
### ---- Solution begin ----
# Construct the A matrix and the b vector
for i in range(N):
    for j in range(N):
        A[i][j] = rbf(coords[i][:2] - coords[j][:2])
for i in range(N):
    A[i][N] = 1
    A[i][N + 1] = coords[i][0]
    A[i][N + 2] = coords[i][1]
for j in in range(N):
    A[N][j] = 1
    A[N+1][j] = coords[i][0]
    A[N+2][j] = coords[i][1]
# Solve for the rbf coefficients
s_height = np.linalg.solve(A, b)
### --------



def rbf_height_fun(x,y):
    ### ---- Insert code here ----
    radials = [rbf(np.array([x, y]) - p_coords[:2]) for p_coords in coords]
    p_vector = [[1, coords[i][0], coords[i][1]] for i in range(len(coords))]

    h = np.dot(radials, np.append(s_height, np.append(radials, p_vector))

    ### --------

XV,YV,ZV= make_grid((0,spanx/span),(0,spany/span), rbf_height_fun)
draw_hm(XV,YV,ZV)

IndentationError: expected an indented block (1092849744.py, line 26)

## Questions:

- Write your observations regarding the difference between Gaussian and Thin Plate Spline radial basis functions.
- Is it possible to represent a constant height function using Gaussian radial basis functions?
- What is the effect of changing the `inv_scale` factor? In particular, what happens when `inv_scale` is set to something very large?
- Why do we add the polynomial terms in the case of Thin Plate Spline RBFs?
- What would you say are the main trade-offs, i.e. pros and cons regarding the RBF method in general? (Hint: you can think beyond 2D)